In [17]:
import pandas as pd
import geopandas as gpd

import folium
from folium import plugins
from folium.plugins.draw import Draw

import fiona
#import json
#import geojson
import branca
from shapely.geometry import *

from ipywidgets import Text, HTML

'''


Datenverwaltung

'''
#Paths
geo_daten = r"C:\Users\Kayla\Documents\GitHub\gis-projekt\Data\Landkreise_DE.geojson"
bev_daten = r"C:\Users\Kayla\Documents\GitHub\gis-projekt\Data\bev_landkreis.csv"


#Geodaten: Landkreise + BKA Daten (JOINED)
df = gpd.read_file(geo_daten)
df.head()

#Relevante Daten aus dem Dataframe laden 
landkreise = df[['GEN', 'geometry']]
landkreise.set_index('GEN')
landkreise.head()

#Stats
df_2 = pd.read_table(bev_daten)
df_2.head()

#Kriminalitätsdaten 
krimi_daten = df_2.copy()
krimi_daten.head()

#obj_int = {'erfasste_Faelle': int} #erfasste_Faelle wird als Object kopiert. Muss wieder als INT gespeichert werden
#krimi_daten = krimi_daten.astype(obj_int)

stats = krimi_daten

stats['krimi'] = (krimi_daten['erfasste_Faelle']/krimi_daten['bev']) * 100000

#Testing
#display(krimi_daten)


#Mittelpunkte der Polygone (pro Landkreise)
punkte = df[['GEN','geometry']].copy()
punkte['geometry'] = punkte['geometry'].centroid
punkte.head()

#Testing
#display(punkte)

'''
Basiskarten/ Kartenlayer
'''
location = [51.133481, 10.018343]
zoom = 6


k = folium.Map(
    location=location, 
    zoom_start=zoom)

folium.TileLayer('Cartodb Positron').add_to(k)


# Daten Kartenlayer
folium.GeoJson(geo_daten, 
               name="Landkreise",
               show = False,
              ).add_to(k)

# Feature Groups
#fg = folium.FeatureGroup(name='My Feature Group', show=False)


# Extras/ Plugins
fs_plugin = plugins.Fullscreen()

# Children
k.add_child(fg)
k.add_child(fs_plugin)

'''
Info Layer - Krimi.-Choroplethenkarte
'''

#Choroplethenkarte

folium.Choropleth(geo_data=geo_daten,
             data=stats,
             columns=['GEN', 'krimi'],
             key_on='feature.properties.GEN',
             fill_opacity=0.7, line_opacity=0.2,
             fill_color = 'PuRd',
             legend_name='Allgemeine Kriminalität pro Landkreis (pro 100.000 Einwohner)',
                 name='Krimi Statistik').add_to(k)

'''
Interaktive Widgets
'''
#Draw

poi= Draw()
poi.add_to(k)

'''
Display: Karte + Widgets
'''

#Layer Control für Karte
folium.LayerControl().add_to(k)

#To do: Tabllen, Widgets + Tabs

k

In [ ]:
#df.isnull().values.any()
#df.dtypes
#krimi_daten.dtypes
krimi_daten
#stats.dtypes

df
#landkreise
#gfg_csv_data = stats.to_csv('stats.csv', index = False) 